# Todo

- [ ] Adding metainformation semester and type of exchange from mainpage to the records, because not represented in the detail page
- [ ] Fixing out of index error in the loop
- [ ] Shorter versions of reports
- [ ] reports that only provide metadata
- [ ] reports that have more metadata than normally, e.g. campus

In [2]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd
import datetime
import time

In [3]:
with open(r"C:/Users/frede/Desktop/Mobility-Online Portal.htm") as fp:
    soup = BeautifulSoup(fp, 'html.parser')

In [4]:
soup

<!DOCTYPE html>

<html><head>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<meta content="max-age=0, no-chache, must-revalidate" http-equiv="cache-control"/>
<meta content="no-cache" http-equiv="pragma"/>
<meta content="de" http-equiv="language"/><meta content="0" http-equiv="expires"/><meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta content="SOP Hilmbauer &amp; Mauberger GmbH &amp; CoKG" name="author"/>
<meta content="SOP Hilmbauer &amp; Mauberger GmbH &amp; CoKG" name="copyright"/>
<meta content="Erasmus, Student Exchange, UniversitÃ¤t Mannheim" name="page-topic"/>
<meta content="The High-End Standard Software for the web-based management of international educational cooperation and all types of academic mobilities" name="description"/>
<meta content="Mobility, Erasmus, Tool, Erasmus+, UniversitÃ¤t Mannheim" name="keywords"/>
<meta content="index,nofollow" name="robots"/>
<title>Mobility-Online Portal</title>
<title>Mobility-Online

Results containing all links from the mainpage to the individual records

In [5]:
results = soup.find_all("a", string="")

In [6]:
# 1. HTTPS-Link regex finder
# 2. replace &-symbol with correct representation
# 3. cut off the "-symbols

# Output: List with urls to all reports - clean_links
clean_links = []
len_results = len(results)
for i in range(2, len(results) - 1):
    clean_links.append(re.findall(r'"https?:\/\/[^\s]+', str(results[i]).replace(r"&amp;", r"&"))[0].replace('"', ''))

IndexError: list index out of range

In [19]:
clean_links[7328]

'https://www.service4mobility.com/mannheim/DispQuestionServlet?identifier=MANNHEI01&kz_call=A&sprache=de&org_id=72&q_set_nr=ERFAHRUNGSBERICHT&pk_table_name=bewerbung&pk_name=bew_id&inst_id_logo=413686&use_jsp=1&pk_id=211878&bew_id=211878'

In [16]:
r = requests.get(clean_links[7328])

In [17]:
bs_report = BeautifulSoup(r.content, 'html.parser')

In [18]:
bs_report


<!DOCTYPE html>

<html>
<head>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<!----------------
			Styles		
----------------->
<link href="./stylesheets/bootstrap/bootstrap-5.1.3-dist/bootstrap.min.css" rel="stylesheet" type="text/css"/>
<link href="./stylesheets/fontawesome/fontawesome-free-6.4.0-web/css/fontawesome.min.css" rel="stylesheet" type="text/css"/>
<link href="./stylesheets/fontawesome/fontawesome-free-6.4.0-web/css/regular.min.css" rel="stylesheet" type="text/css"/>
<link href="./stylesheets/fontawesome/fontawesome-free-6.4.0-web/css/solid.min.css" rel="stylesheet" type="text/css"/>
<link href="./stylesheets/fontawesome/fontawesome-free-6.4.0-web/css/v5-font-face.min.css" rel="stylesheet" type="text/css"/>
<link href="./stylesheets/fontawesome/fontawesome-free-6.4.0-web/css/fontawesome-custom.css" rel="stylesheet" type="text/css"/>
<link href="./stylesheets/sopValidateBootstrapForm.css" rel="stylesheet" type="text/css"/>
<link href="./stylesheets/da

Retrieve meta infroamtion like uni, semester, etc.

0 - Land der Gastinstitution

1 - Gastinstitution

2 - Studienjahr

3 - Fakultaet

4 - Studiengang

5 - Verfasser-ID

In [21]:
bs_report.find_all("div", class_="bt-collapsible-card-body card-body")

[<div class="bt-collapsible-card-body card-body">
 	      Südkorea
 	    </div>,
 <div class="bt-collapsible-card-body card-body">
 	      KRSEOUL01 - KAIST College of Business
 	    </div>,
 <div class="bt-collapsible-card-body card-body">
 	      2016/2017
 	    </div>,
 <div class="bt-collapsible-card-body card-body">
 	      Fakultät für Betriebswirtschaftslehre - BWL
 	    </div>,
 <div class="bt-collapsible-card-body card-body">
 	      Management (MMM), Master - BWL_M_BWL
 	    </div>,
 <div class="bt-collapsible-card-body card-body">
 	      267166
 	    </div>,
 <div class="bt-collapsible-card-body card-body">
 </div>,
 <div class="bt-collapsible-card-body card-body">
 </div>,
 <div class="bt-collapsible-card-body card-body">
 </div>,
 <div class="bt-collapsible-card-body card-body">
 </div>,
 <div class="bt-collapsible-card-body card-body">
 </div>,
 <div class="bt-collapsible-card-body card-body">
 </div>]

In [22]:
extract_metadata(bs_report)

['Südkorea',
 'KRSEOUL01 - KAIST College of Business',
 '2016/2017',
 'Fakultät für Betriebswirtschaftslehre - BWL',
 'Management (MMM), Master - BWL_M_BWL',
 '267166']

In [8]:
def extract_metadata(soup):
    metadata_list = []
    metadata = soup.find_all("div", class_="bt-collapsible-card-body card-body")
    for i in range(0,6):
        clean_string = re.sub(r"\r\n\t", "", metadata[i].text)
        clean_string = re.sub(r"  ", "", clean_string)
        metadata_list.append(clean_string)
    return metadata_list

#### Main text

0 - Vorbereitung

1 - Unterkunft

2 - Studium

3 - Freizeit

4 - Budget

5 - Tipps zur Finanzierung

6 - Kurswahl

7 - Fazit

In [23]:
bs_report.find_all(id=re.compile("plain_text"))

[<span id="plain_text_zu_q_set_id_6693">Da das KAIST College of Business als offizielle Partneruniversität der Uni Mannheim gelistet ist, verlief der Bewerbungsprozess unkompliziert. Mit der Zusage vom akademischen Auslandsamt wurde auch eine Liste mit allen notwendigen Nachweisen und Formalitäten versandt. Die eigentliche Auswahl für den Platz im Austauschprogramm wurde von der Uni Mannheim übernommen, bevor die persönlichen Details der Teilnehmer dann an den KAIST Ansprechpartner übermittelt wurden. Die Auslandskoordinatorin in Seoul, Ms. Ji Eun Lee, übernahm daraufhin die Kommunikation und stand in sämtlichen Fragen zur Vorbereitung und Planung des Aufenthaltes mit Rat und Tat zur Seite. Zunächst musste eine vorläufige Liste der gewünschten Kurse an Sie geschickt werden, welche jedoch nur eine erste Orientierung darstellte, da sich die Liste der angebotenen Kurse im Nachhinein noch mehrfach änderte. Das endgültige Kursangebot stand erst circa einen Monat vor Beginn des Auslandssemes

In [26]:
extract_maintext(bs_report)

['Da das KAIST College of Business als offizielle Partneruniversität der Uni Mannheim gelistet ist, verlief der Bewerbungsprozess unkompliziert. Mit der Zusage vom akademischen Auslandsamt wurde auch eine Liste mit allen notwendigen Nachweisen und Formalitäten versandt. Die eigentliche Auswahl für den Platz im Austauschprogramm wurde von der Uni Mannheim übernommen, bevor die persönlichen Details der Teilnehmer dann an den KAIST Ansprechpartner übermittelt wurden. Die Auslandskoordinatorin in Seoul, Ms. Ji Eun Lee, übernahm daraufhin die Kommunikation und stand in sämtlichen Fragen zur Vorbereitung und Planung des Aufenthaltes mit Rat und Tat zur Seite. Zunächst musste eine vorläufige Liste der gewünschten Kurse an Sie geschickt werden, welche jedoch nur eine erste Orientierung darstellte, da sich die Liste der angebotenen Kurse im Nachhinein noch mehrfach änderte. Das endgültige Kursangebot stand erst circa einen Monat vor Beginn des Auslandssemesters fest. In jedem Fall musste für de

maintext method has to be adjusted for some reports because they are missing the fields budget and financing, therefore the range is 0,6 and not 0,8 like for the rest of the reports

In [25]:
def extract_maintext(soup):
    maintext_list = []
    maintext = soup.find_all(id=re.compile("plain_text"))
    for i in range(0,6):
        maintext_list.append(maintext[i].text)
    return maintext_list

Bei folgenden Links fallen die Kategorien Budget und Finanzierung weg und können daher nicht korrekt geparset werden

- [x] clean_links[4171]

- [x] clean_links[4406]

- [x] clean_links[4829]

- [x] clean_links[4870]


- [x] 4938 - 5428

- [x] 7424 - 7398

- [x] 7396 - 7341

- [x] 7339 - 7331

- [x] 7328 - 7230

6664 - 6661, 6590, 6581, 6482 -> Haben gar keine Eintraege nur metadaten

- [x] 5826 - 5705

- [x] 5703 - 5667

- [x] 5665 - 5447

- [x] 5445

- [x] 5443, 5442

- [x] 5440 - 5430

In [43]:
clean_links[6590]

'https://www.service4mobility.com/mannheim/DispQuestionServlet?identifier=MANNHEI01&kz_call=A&sprache=de&org_id=72&q_set_nr=ERFAHRUNGSBERICHT&pk_table_name=bewerbung&pk_name=bew_id&inst_id_logo=413686&use_jsp=1&pk_id=220645&bew_id=220645'

In [58]:
for i in range(4870, 4871):
    try:
        url = clean_links[i]
        r = requests.get(url)
        soup = BeautifulSoup(r.content, 'html.parser')
        report = extract_metadata(soup) + extract_maintext(soup) + [str(url)] + [str(datetime.datetime.now())]
        reports.append(report)
        print(i)
        time.sleep(0.2)
    except IndexError:
        print("Error occured while parsing following file: " + str(i))

4870


In [59]:
len(reports)

1069

### Store to dataframe

In [44]:
d = {'Id': [], 'Land der Gastinstitution': [], 'Gastinstitution': [], 'Studienjahr': [], 'Fakultaet': [], 'Studiengang': [], 'Verfasser-ID': [], 'Vorbereitung': [], 'Unterkunft': [], 'Studium': [], 'Freizeit': [], 'Budget': [], 'Finanzierung': [], 'Kurswahl': [], 'Fazit': [], 'url': [],'downloaded': [] }

In [61]:
df = pd.DataFrame(reports, columns=['Land der Gastinstitution', 'Gastinstitution', 'Studienjahr', 'Fakultaet', 'Studiengang', 'Verfasser-ID', 'Vorbereitung', 'Unterkunft', 'Studium', 'Freizeit', 'Kurswahl', 'Fazit', 'url','downloaded'])

In [60]:
df = pd.DataFrame(reports, columns=['Land der Gastinstitution', 'Gastinstitution', 'Studienjahr', 'Fakultaet', 'Studiengang', 'Verfasser-ID', 'Vorbereitung', 'Unterkunft', 'Studium', 'Freizeit', 'Budget', 'Finanzierung', 'Kurswahl', 'Fazit', 'url','downloaded'])

ValueError: 16 columns passed, passed data had 14 columns

In [63]:
df.head()

Land der Gastinstitution                                    Gastinstitution  \
0                   Kanada  CAVERSCHIEDENE01 - LP Ontario (Koordinierungss...   
1     China, Volksrepublik                   CNHONGKON08 - Lingnan University   
2               Frankreich                   FRANGERS01 - Université d`Angers   
3               Frankreich  FRNANCY43-2 - Université de Lorraine - Campus ...   
4               Frankreich       FRTOULOUS01 - Université Toulouse 1 Capitole   

  Studienjahr                       Fakultaet  \
0   2016/2017  Philosophische Fakultät - PHIL   
1   2016/2017  Philosophische Fakultät - PHIL   
2   2016/2017                               -   
3   2016/2017                               -   
4   2016/2017                               -   

                                         Studiengang  \
0  Current English Linguistics and Literary Studi...   
1  Geschichte: Kultur und Wirtschaft, Bachelor - ...   
2                Abteilung Rechtswissenschaft - JURA   
3                Abteilung Rechtswissenschaft - JURA   
4                Abteilung Rechtswissenschaft - JURA   

                                        Verfasser-ID  \
0                                             266308   
1                                             266290   
2  Kombinationsstudiengang Unternehmensjurist/in,...   
3  Kombinationsstudiengang Unternehmensjurist/in,...   
4  Kombinationsstudiengang Unternehmensjurist/in,...   

                                        Vorbereitung  \
0  Die Bewerbung bei der Gasthochschule war bei m...   
1  Ich habe das HWS 16/17 und das FSS 17 an der L...   
2  Die Bewerbung begann mit dem Einreichen der Be...   
3  Für mich stand schon seit Beginn meines Studiu...   
4  Seit Beginn meines Studiums stand für mich fes...   

                                          Unterkunft  \
0  Ich habe in einer WG in einem kleinen Haus gew...   
1  Die Austauschstudenten werden per Losverfahren...   
2  Wie bereits angesprochen, habe ich im Wohnheim...   
3  Für die Unterbringung gibt es zwei Optionen: e...   
4  Beim Online-Anmeldeformular der Gastuniversitä...   

                                             Studium  \
0  Das Studium allgemein ist deutlich stressiger ...   
1  Kurse\r\nWas das Kursangebot angeht war ich re...   
2  Die bekanntesten rechtswissenschaftlichen Faku...   
3  An der Gasthochschule gab es zunächst einen „W...   
4  Der Kurskatalog der UT1 war vor Beginn des Aus...   

                                            Freizeit  \
0  In meiner Freizeit habe ich viel zeit mit mein...   
1  Was die Lebenshaltungskosten angeht, so sind d...   
2  Angers ist eine wunderschöne und auch wohlhabe...   
3  Der Alltag in Nancy in Nancy lässt sich vielse...   
4  Lebensunterhaltskosten sind teurer in Frankrei...   

                                            Kurswahl  \
0  The Culture of Leadership/ English/ Prüfung: P...   
1  Die Kurse waren alle auf Englisch, die Anerken...   
2  1. Semester\r\n\r\nPhilosophie du Droit / 2 EC...   
3  UFD 11 / Droit constitutionnel avec TD / 7 ECT...   
4  Institutions Internationales / 4 ECTS / mdl. P...   

                                               Fazit  \
0  Meine schönsten Erfahrungen verbinde ich mit d...   
1  Abschließend kann ich nur sagen, dass ich die ...   
2  Vor meinem Auslandssemester dachte ich, dass e...   
3  Natürlich habe ich während meines Erasmus-Jahr...   
4  Ich habe schlechte Erfahrung mit der französis...   

                                                 url  \
0  https://www.service4mobility.com/mannheim/Disp...   
1  https://www.service4mobility.com/mannheim/Disp...   
2  https://www.service4mobility.com/mannheim/Disp...   
3  https://www.service4mobility.com/mannheim/Disp...   
4  https://www.service4mobility.com/mannheim/Disp...   

                   downloaded  
0  2024-04-22 09:26:25.573981  
1  2024-04-22 09:26:26.179389  
2  2024-04-22 09:26:26.778390  
3  2024-04-22 09:26:27.400836  
4  2024-04-22 09:26:28.2705

In [64]:
df.to_csv("short version study reports.csv", sep=";")